# `fsspec-reference-maker` tutorial

Created June 8th, 2020 by [Lucas Sterzinger](mailto:lsterzinger@ucdavis.edu) ([Twitter](https://twitter.com/lucassterzinger)) as part of the NCAR [Summer Internship in Parallel Computational Science (SIParCS)](https://www2.cisl.ucar.edu/siparcs)

If any part of this tutorial is now out of date, please feel free to open a pull request with a fix

In [2]:
from fsspec_reference_maker.hdf import SingleHdf5ToZarr 
from fsspec_reference_maker.combine import MultiZarrToZarr

## Create metadata JSONs

### This function returns a list of S3 files for a given satellite, year, and day

In [3]:
import xarray as xr
import numpy as np
import matplotlib.pyplot as plt
import s3fs
import datetime as dt
import zipfile
import logging
import fsspec
import json
from tqdm import tqdm
from glob import glob

In [6]:
def get_file_list(sat,lyr,idyjl):
    # arguments
    # sat   goes-east,goes-west,himawari
    # lyr   year
    # idyjl day of year
    
    d = dt.datetime(lyr,1,1) + dt.timedelta(days=idyjl)
    fs = s3fs.S3FileSystem(anon=True) #connect to s3 bucket!

    #create strings for the year and julian day
    imon,idym=d.month,d.day
    syr,sjdy,smon,sdym = str(lyr).zfill(4),str(idyjl).zfill(3),str(imon).zfill(2),str(idym).zfill(2)
    
    #use glob to list all the files in the directory
    if sat=='goes-east':
        file_location,var = fs.glob('s3://noaa-goes16/ABI-L2-SSTF/'+syr+'/'+sjdy+'/*/*.nc'),'SST'
    if sat=='goes-west':
        file_location,var = fs.glob('s3://noaa-goes17/ABI-L2-SSTF/'+syr+'/'+sjdy+'/*/*.nc'),'SST'
    if sat=='himawari':
        file_location,var = fs.glob('s3://noaa-himawari8/AHI-L2-FLDK-SST/'+syr+'/'+smon+'/'+sdym+'/*/*L2P*.nc'),'sea_surface_temperature'
    
    return file_location

In [9]:
flist = get_file_list("goes-east", 2020, 210)
urls = ["s3://" + f for f in flist]

### This function creates JSON metadata files for each of the S3 files in the local `jsons/` directory

These files point to the S3 location of the netCDF files, and only need to be created once. Tihs process took me about 10 minutes to generate the JSONs for 24 files. This function could easily be made to run in parallel for faster performance

In [8]:
def gen_json(urllist):
    so = dict(
        mode="rb", anon=True, default_fill_cache=False, default_cache_type="none"
    )
    zf = zipfile.ZipFile("out.zip", mode="w")
    for u in tqdm(urllist):
        with fsspec.open(u, **so) as inf:
            h5chunks = SingleHdf5ToZarr(inf, u, xarray=True, inline_threshold=100)
            with zf.open(os.path.basename(u) + ".json", 'w') as outf:
                outf.write(json.dumps(h5chunks.translate()).encode())

    # for u in tqdm(urllist):
    #     with fsspec.open(u, **so) as f:
    #         h5chunks = fsshdf.SingleHdf5ToZarr(f, u, xarray=True)
    #         j = h5chunks.translate()
    #         fname = u.split("/")[7]
    #         with open(f"./jsons/{fname}.json", "w") as fout:
    #             fout.write(json.dumps(j))


In [15]:
gen_json(urls)

  0%|          | 0/24 [00:26<?, ?it/s]


KeyboardInterrupt: 

***
## Read remote netCDF files with xarray and fsspec

### First, create a list of JSON files

In [3]:
json_list = sorted(glob("./jsons/*.json"))

### Then, loop over the files and use `fsspec.get_mapper()` to create mappers for each file object, creating a list of mappers

In [4]:
mzz = MultiZarrToZarr(
    # "./jsons/*.json",
    "zip://*.json::out.zip",
    remote_protocol="s3",
    remote_options={'anon':True},
    xarray_kwargs={
        "decode_cf" : False,
        "mask_and_scale" : False,
        "decode_times" : False,
        "decode_timedelta" : False,
        "use_cftime" : False,
        "decode_coords" : False
    },
    with_mf='t'
)

In [6]:
%%time
mzz.translate("combined.json")

CPU times: user 20.6 s, sys: 685 ms, total: 21.3 s
Wall time: 40 s


In [7]:
%%time
fs = fsspec.filesystem("reference", fo="./goes.json", remote_protocol="s3", 
                        remote_options={"anon":True}, skip_instance_cache=True)
m = fs.get_mapper("")
ds = xr.open_dataset(m, engine='zarr')

CPU times: user 11.9 s, sys: 148 ms, total: 12 s
Wall time: 13.8 s


In [8]:
ds

<xarray.Dataset>
Dimensions:                                                 (SST_day_night_emissive_bands: 4, SST_night_only_emissive_band: 1, number_of_LZA_bounds: 2, number_of_SZA_bounds: 2, number_of_image_bounds: 2, number_of_time_bounds: 2, t: 24, x: 5424, y: 5424)
Coordinates: (12/14)
    SST_day_night_emissive_band_ids                         (t, SST_day_night_emissive_bands) float32 ...
    SST_day_night_emissive_wavelengths                      (t, SST_day_night_emissive_bands) float32 ...
    SST_night_only_emissive_band_id                         (SST_night_only_emissive_band) float32 ...
    SST_night_only_emissive_wavelength                      (t, SST_night_only_emissive_band) float32 ...
    day_solar_zenith_angle                                  (t) float32 ...
    night_solar_zenith_angle                                (t) float32 ...
    ...                                                      ...
    retrieval_solar_zenith_angle                            (t) float32 ...
  * t                                                       (t) datetime64[ns] ...
  * x                                                       (x) float32 -0.15...
    x_image                                                 float32 ...
  * y                                                       (y) float32 0.151...
    y_image                                                 float32 ...
Dimensions without coordinates: SST_day_night_emissive_bands, SST_night_only_emissive_band, number_of_LZA_bounds, number_of_SZA_bounds, number_of_image_bounds, number_of_time_bounds
Data variables: (12/42)
    DQF                                                     (t, y, x) float32 ...
    SST                                                     (t, y, x) float32 ...
    algorithm_dynamic_input_data_container                  (t) float64 ...
    algorithm_product_version_container                     (t) float64 ...
    day_solar_zenith_angle_bounds                           (t, number_of_SZA_bounds) float32 ...
    geospatial_lat_lon_extent                               (t) float32 ...
    ...                                                      ...
    total_number_of_severely_degraded_quality_ocean_pixels  (t) float64 ...
    total_number_of_unprocessed_pixels                      (t) float64 ...
    twilight_solar_zenith_angle                             (t) float32 ...
    twilight_solar_zenith_angle_bounds                      (t, number_of_SZA_bounds) float32 ...
    x_image_bounds                                          (number_of_image_bounds) float32 ...
    y_image_bounds                                          (number_of_image_bounds) float32 ...
Attributes: (12/34)
    Conventions:               CF-1.7
    Metadata_Conventions:      Unidata Dataset Discovery v1.0
    _FillValue:                -999.0
    cdm_data_type:             Image
    cell_methods:              quantitative_local_zenith_angle: sum retrieval...
    dataset_name:              OR_ABI-L2-SSTF-M6_G16_s20202100000205_e2020210...
    ...                        ...
    summary:                   The ABI Sea Surface Temperature (SST) is calcu...
    time_coverage_end:         2020-07-28T00:59:51.3Z
    time_coverage_start:       2020-07-28T00:00:20.5Z
    timeline_id:               ABI Mode 6
    title:                     ABI L2 Sea Surface (Skin) Temperature
    units:                     K

In [11]:
import hvplot.xarray

In [13]:
ds.SST.isel(t=0).hvplot.image(x='x', y='y', rasterize=True, aspect='equal', cmap='turbo')

:DynamicMap   []
   :Image   [x,y]   (SST)

### Take a subset of the data (in this case, the Gulf Stream)

### Select a single time with `.isel(t=14)`

In [ ]:
%%time
subset = ds.sel(x=slice(-0.01,0.07215601),y=slice(0.12,0.09))  #reduce to GS region

masked = subset.SST.where(subset.DQF==0)

masked.isel(t=14).plot(vmin=14+273.15,vmax=30+273.15,cmap='inferno')

### Plot a mean along the time axis (1-day average)

In [ ]:
%%time
subset = ds.sel(x=slice(-0.01,0.07215601),y=slice(0.12,0.09))  #reduce to GS region

masked = subset.SST.where(subset.DQF==0)

masked.mean("t", skipna=True).plot(vmin=14+273.15,vmax=30+273.15,cmap='inferno')